In [29]:
from datetime import datetime
import gradio as gr
import requests
from Bio.PDB import PDBParser, MMCIFParser, PDBIO, Select
from Bio.PDB.Polypeptide import is_aa
from Bio.SeqUtils import seq1
from typing import Optional, Tuple
import numpy as np
import os
from gradio_molecule3d import Molecule3D

#from model_loader import load_model

import torch
import torch.nn as nn
import torch.nn.functional as F
from torch.utils.data import DataLoader

import re
import pandas as pd
import copy

#import transformers
#from transformers import AutoTokenizer, DataCollatorForTokenClassification

#from datasets import Dataset

from scipy.special import expit

def normalize_scores(scores):
    min_score = np.min(scores)
    max_score = np.max(scores)
    return (scores - min_score) / (max_score - min_score) if max_score > min_score else scores

def read_mol(pdb_path):
    """Read PDB file and return its content as a string"""
    with open(pdb_path, 'r') as f:
        return f.read()

def fetch_structure(pdb_id: str, output_dir: str = ".") -> Optional[str]:
    """
    Fetch the structure file for a given PDB ID. Prioritizes CIF files.
    If a structure file already exists locally, it uses that.
    """
    file_path = download_structure(pdb_id, output_dir)
    if file_path:
        return file_path
    else:
        return None

def download_structure(pdb_id: str, output_dir: str) -> Optional[str]:
    """
    Attempt to download the structure file in CIF or PDB format.
    Returns the path to the downloaded file, or None if download fails.
    """
    for ext in ['.cif', '.pdb']:
        file_path = os.path.join(output_dir, f"{pdb_id}{ext}")
        if os.path.exists(file_path):
            return file_path
        url = f"https://files.rcsb.org/download/{pdb_id}{ext}"
        try:
            response = requests.get(url, timeout=10)
            if response.status_code == 200:
                with open(file_path, 'wb') as f:
                    f.write(response.content)
                return file_path
        except Exception as e:
            print(f"Download error for {pdb_id}{ext}: {e}")
    return None

def convert_cif_to_pdb(cif_path: str, output_dir: str = ".") -> str:
    """
    Convert a CIF file to PDB format using BioPython and return the PDB file path.
    """
    pdb_path = os.path.join(output_dir, os.path.basename(cif_path).replace('.cif', '.pdb'))
    parser = MMCIFParser(QUIET=True)
    structure = parser.get_structure('protein', cif_path)
    io = PDBIO()
    io.set_structure(structure)
    io.save(pdb_path)
    return pdb_path

def fetch_pdb(pdb_id):
    pdb_path = fetch_structure(pdb_id)
    if not pdb_path:
        return None
    _, ext = os.path.splitext(pdb_path)
    if ext == '.cif':
        pdb_path = convert_cif_to_pdb(pdb_path)
    return pdb_path

def create_chain_specific_pdb(input_pdb: str, chain_id: str, residue_scores: list, protein_residues: list) -> str:
    """
    Create a PDB file with only the selected chain and residues, replacing B-factor with prediction scores
    """
    # Read the original PDB file
    parser = PDBParser(QUIET=True)
    structure = parser.get_structure('protein', input_pdb)
    
    # Prepare a new structure with only the specified chain and selected residues
    output_pdb = f"{os.path.splitext(input_pdb)[0]}_{chain_id}_predictions_scores.pdb"
    
    # Create scores dictionary for easy lookup
    scores_dict = {resi: score for resi, score in residue_scores}

    # Create a custom Select class
    class ResidueSelector(Select):
        def __init__(self, chain_id, selected_residues, scores_dict):
            self.chain_id = chain_id
            self.selected_residues = selected_residues
            self.scores_dict = scores_dict
        
        def accept_chain(self, chain):
            return chain.id == self.chain_id
        
        def accept_residue(self, residue):
            return residue.id[1] in self.selected_residues

        def accept_atom(self, atom):
            if atom.parent.id[1] in self.scores_dict:
                atom.bfactor = np.absolute(1-self.scores_dict[atom.parent.id[1]]) * 100
            return True

    # Prepare output PDB with selected chain and residues, modified B-factors
    io = PDBIO()
    selector = ResidueSelector(chain_id, [res.id[1] for res in protein_residues], scores_dict)
    
    io.set_structure(structure[0])
    io.save(output_pdb, selector)
    
    return output_pdb

def process_pdb(pdb_id_or_file, segment):
    # Determine if input is a PDB ID or file path
    if pdb_id_or_file.endswith('.pdb'):
        pdb_path = pdb_id_or_file
        pdb_id = os.path.splitext(os.path.basename(pdb_path))[0]
    else:
        pdb_id = pdb_id_or_file
        pdb_path = fetch_pdb(pdb_id)
    
    if not pdb_path:
        return "Failed to fetch PDB file", None, None
    
    # Determine the file format and choose the appropriate parser
    _, ext = os.path.splitext(pdb_path)
    parser = MMCIFParser(QUIET=True) if ext == '.cif' else PDBParser(QUIET=True)
    
    try:
        # Parse the structure file
        structure = parser.get_structure('protein', pdb_path)
    except Exception as e:
        return f"Error parsing structure file: {e}", None, None
    
    # Extract the specified chain
    try:
        chain = structure[0][segment]
    except KeyError:
        return "Invalid Chain ID", None, None
    
    protein_residues = [res for res in chain if is_aa(res)]
    sequence = "".join(seq1(res.resname) for res in protein_residues)
    sequence_id = [res.id[1] for res in protein_residues]

    visualized_sequence = "".join(seq1(res.resname) for res in protein_residues)
    if sequence != visualized_sequence:
        raise ValueError("The visualized sequence does not match the prediction sequence")
        
    scores = np.random.rand(len(sequence))
    normalized_scores = normalize_scores(scores)
    
    # Zip residues with scores to track the residue ID and score
    residue_scores = [(resi, score) for resi, score in zip(sequence_id, normalized_scores)]

    
    # Define the score brackets
    score_brackets = {
        "0.0-0.2": (0.0, 0.2),
        "0.2-0.4": (0.2, 0.4),
        "0.4-0.6": (0.4, 0.6),
        "0.6-0.8": (0.6, 0.8),
        "0.8-1.0": (0.8, 1.0)
    }
    
    # Initialize a dictionary to store residues by bracket
    residues_by_bracket = {bracket: [] for bracket in score_brackets}
    
    # Categorize residues into brackets
    for resi, score in residue_scores:
        for bracket, (lower, upper) in score_brackets.items():
            if lower <= score < upper:
                residues_by_bracket[bracket].append(resi)
                break
    
    # Preparing the result string
    current_time = datetime.now().strftime("%Y-%m-%d %H:%M:%S")
    result_str = f"Prediction for PDB: {pdb_id}, Chain: {segment}\nDate: {current_time}\n\n"
    result_str += "Residues by Score Brackets:\n\n"
    
    # Add residues for each bracket
    for bracket, residues in residues_by_bracket.items():
        result_str += f"Bracket {bracket}:\n"
        result_str += "Columns: Residue Name, Residue Number, One-letter Code, Normalized Score\n"
        result_str += "\n".join([
            f"{res.resname} {res.id[1]} {sequence[i]} {normalized_scores[i]:.2f}" 
            for i, res in enumerate(protein_residues) if res.id[1] in residues
        ])
        result_str += "\n\n"

    # Create chain-specific PDB with scores in B-factor
    scored_pdb = create_chain_specific_pdb(pdb_path, segment, residue_scores, protein_residues)

    # Molecule visualization with updated script with color mapping
    mol_vis = molecule(pdb_path, residue_scores, segment)#, color_map)

    # Improved PyMOL command suggestions
    current_time = datetime.now().strftime("%Y-%m-%d %H:%M:%S")
    pymol_commands = f"Prediction for PDB: {pdb_id}, Chain: {segment}\nDate: {current_time}\n\n"
    
    pymol_commands += f"""
    # PyMOL Visualization Commands
    load {os.path.abspath(pdb_path)}, protein
    hide everything, all
    show cartoon, chain {segment}
    color white, chain {segment}
    """
    
    # Define colors for each score bracket
    bracket_colors = {
        "0.0-0.2": "white",
        "0.2-0.4": "lightorange",
        "0.4-0.6": "orange",
        "0.6-0.8": "orangered",
        "0.8-1.0": "red"
    }
    
    # Add PyMOL commands for each score bracket
    for bracket, residues in residues_by_bracket.items():
        if residues:  # Only add commands if there are residues in this bracket
            color = bracket_colors[bracket]
            resi_list = '+'.join(map(str, residues))
            pymol_commands += f"""
    select bracket_{bracket.replace('.', '').replace('-', '_')}, resi {resi_list} and chain {segment}
    show sticks, bracket_{bracket.replace('.', '').replace('-', '_')}
    color {color}, bracket_{bracket.replace('.', '').replace('-', '_')}
    """
    
    # Create prediction and scored PDB files
    prediction_file = f"{pdb_id}_binding_site_residues.txt"
    with open(prediction_file, "w") as f:
        f.write(result_str)
    
    return pymol_commands, mol_vis, [prediction_file,scored_pdb]

def molecule(input_pdb, residue_scores=None, segment='A'):
    # More granular scoring for visualization
    mol = read_mol(input_pdb)  # Read PDB file content

    # Prepare high-scoring residues script if scores are provided
    high_score_script = ""
    if residue_scores is not None:
        # Filter residues based on their scores
        class1_score_residues = [resi for resi, score in residue_scores if 0.0 < score <= 0.2]
        class2_score_residues = [resi for resi, score in residue_scores if 0.2 < score <= 0.4]
        class3_score_residues = [resi for resi, score in residue_scores if 0.4 < score <= 0.6]
        class4_score_residues = [resi for resi, score in residue_scores if 0.6 < score <= 0.8]
        class5_score_residues = [resi for resi, score in residue_scores if 0.8 < score <= 1.0]
        
        high_score_script = """
        // Load the original model and apply white cartoon style
        let chainModel = viewer.addModel(pdb, "pdb");
        chainModel.setStyle({}, {});
        chainModel.setStyle(
            {"chain": "%s"}, 
            {"cartoon": {"color": "white"}}
        );

        // Create a new model for high-scoring residues and apply red sticks style
        let class1Model = viewer.addModel(pdb, "pdb");
        class1Model.setStyle({}, {});
        class1Model.setStyle(
            {"chain": "%s", "resi": [%s]}, 
            {"stick": {"color": "0xFFFFFF", "opacity": 0.5}}
        );

        // Create a new model for high-scoring residues and apply red sticks style
        let class2Model = viewer.addModel(pdb, "pdb");
        class2Model.setStyle({}, {});
        class2Model.setStyle(
            {"chain": "%s", "resi": [%s]}, 
            {"stick": {"color": "0xFFD580", "opacity": 0.7}}
        );

        // Create a new model for high-scoring residues and apply red sticks style
        let class3Model = viewer.addModel(pdb, "pdb");
        class3Model.setStyle({}, {});
        class3Model.setStyle(
            {"chain": "%s", "resi": [%s]}, 
            {"stick": {"color": "0xFFA500", "opacity": 1}}
        );

        // Create a new model for high-scoring residues and apply red sticks style
        let class4Model = viewer.addModel(pdb, "pdb");
        class4Model.setStyle({}, {});
        class4Model.setStyle(
            {"chain": "%s", "resi": [%s]}, 
            {"stick": {"color": "0xFF4500", "opacity": 1}}
        );

        // Create a new model for high-scoring residues and apply red sticks style
        let class5Model = viewer.addModel(pdb, "pdb");
        class5Model.setStyle({}, {});
        class5Model.setStyle(
            {"chain": "%s", "resi": [%s]}, 
            {"stick": {"color": "0xFF0000", "alpha": 1}}
        );

        """ % (
            segment,
            segment,
            ", ".join(str(resi) for resi in class1_score_residues),
            segment,
            ", ".join(str(resi) for resi in class2_score_residues),
            segment,
            ", ".join(str(resi) for resi in class3_score_residues),
            segment,
            ", ".join(str(resi) for resi in class4_score_residues),
            segment,
            ", ".join(str(resi) for resi in class5_score_residues)
        )
    
    # Generate the full HTML content
    html_content = f"""
    <!DOCTYPE html>
    <html>
    <head>    
        <meta http-equiv="content-type" content="text/html; charset=UTF-8" />
        <style>
        .mol-container {{
            width: 100%;
            height: 700px;
            position: relative;
        }}
        </style>
        <script src="https://cdnjs.cloudflare.com/ajax/libs/jquery/3.6.3/jquery.min.js"></script>
        <script src="https://3Dmol.csb.pitt.edu/build/3Dmol-min.js"></script>
    </head>
    <body>
        <div id="container" class="mol-container"></div>
        <script>
            let pdb = `{mol}`; // Use template literal to properly escape PDB content
            $(document).ready(function () {{
                let element = $("#container");
                let config = {{ backgroundColor: "white" }};
                let viewer = $3Dmol.createViewer(element, config);
                
                {high_score_script}
                
                // Add hover functionality
                viewer.setHoverable(
                    {{}}, 
                    true, 
                    function(atom, viewer, event, container) {{
                        if (!atom.label) {{
                            atom.label = viewer.addLabel(
                                atom.resn + ":" +atom.resi + ":" + atom.atom, 
                                {{
                                    position: atom, 
                                    backgroundColor: 'mintcream', 
                                    fontColor: 'black',
                                    fontSize: 18,
                                    padding: 4
                                }}
                            );
                        }}
                    }},
                    function(atom, viewer) {{
                        if (atom.label) {{
                            viewer.removeLabel(atom.label);
                            delete atom.label;
                        }}
                    }}
                );
                
                viewer.zoomTo();
                viewer.render();
                viewer.zoom(0.8, 2000);
            }});
        </script>
    </body>
    </html>
    """
    
    # Return the HTML content within an iframe safely encoded for special characters
    return f'<iframe width="100%" height="700" srcdoc="{html_content.replace(chr(34), "&quot;").replace(chr(39), "&#39;")}"></iframe>'

# Gradio UI
with gr.Blocks(css="""
    /* Customize Gradio button colors */
    #visualize-btn, #predict-btn {
        background-color: #FF7300; /* Deep orange */
        color: white;
        border-radius: 5px;
        padding: 10px;
        font-weight: bold;
    }
    #visualize-btn:hover, #predict-btn:hover {
        background-color: #CC5C00; /* Darkened orange on hover */
    }
""") as demo:
    gr.Markdown("# Protein Binding Site Prediction")
    
    # Mode selection
    mode = gr.Radio(
        choices=["PDB ID", "Upload File"],
        value="PDB ID",
        label="Input Mode",
        info="Choose whether to input a PDB ID or upload a PDB/CIF file."
    )

    # Input components based on mode
    pdb_input = gr.Textbox(value="2F6V", label="PDB ID", placeholder="Enter PDB ID here...")
    pdb_file = gr.File(label="Upload PDB/CIF File", visible=False)
    visualize_btn = gr.Button("Visualize Structure", elem_id="visualize-btn")

    molecule_output2 = Molecule3D(label="Protein Structure", reps=[
        {
            "model": 0,
            "style": "cartoon",
            "color": "whiteCarbon",
            "residue_range": "",
            "around": 0,
            "byres": False,
        }
    ])

    with gr.Row():
        segment_input = gr.Textbox(value="A", label="Chain ID (protein)", placeholder="Enter Chain ID here...",
        info="Choose in which chain to predict binding sites.")
        prediction_btn = gr.Button("Predict Binding Site", elem_id="predict-btn")

    molecule_output = gr.HTML(label="Protein Structure")
    explanation_vis = gr.Markdown("""
    Score dependent colorcoding:
    - 0.0-0.2: white  
    - 0.2–0.4: light orange  
    - 0.4–0.6: orange
    - 0.6–0.8: orangered
    - 0.8–1.0: red
    """)
    predictions_output = gr.Textbox(label="Visualize Prediction with PyMol")
    gr.Markdown("### Download:\n- List of predicted binding site residues\n- PDB with score in beta factor column")
    download_output = gr.File(label="Download Files", file_count="multiple")
    
    def process_interface(mode, pdb_id, pdb_file, chain_id):
        if mode == "PDB ID":
            return process_pdb(pdb_id, chain_id)
        elif mode == "Upload File":
            _, ext = os.path.splitext(pdb_file.name)
            file_path = os.path.join('./', f"{_}{ext}")
            if ext == '.cif':
                pdb_path = convert_cif_to_pdb(file_path)
            else:
                pdb_path= file_path
            return process_pdb(pdb_path, chain_id)
        else:
            return "Error: Invalid mode selected", None, None

    def fetch_interface(mode, pdb_id, pdb_file):
        if mode == "PDB ID":
            return fetch_pdb(pdb_id)
        elif mode == "Upload File":
            _, ext = os.path.splitext(pdb_file.name)
            file_path = os.path.join('./', f"{_}{ext}")
            #print(ext)
            if ext == '.cif':
                pdb_path = convert_cif_to_pdb(file_path)
            else:
                pdb_path= file_path
            #print(pdb_path)
            return pdb_path
        else:
            return "Error: Invalid mode selected"

    def toggle_mode(selected_mode):
        if selected_mode == "PDB ID":
            return gr.update(visible=True), gr.update(visible=False)
        else:
            return gr.update(visible=False), gr.update(visible=True)

    mode.change(
        toggle_mode,
        inputs=[mode],
        outputs=[pdb_input, pdb_file]
    )

    prediction_btn.click(
        process_interface, 
        inputs=[mode, pdb_input, pdb_file, segment_input], 
        outputs=[predictions_output, molecule_output, download_output]
    )

    visualize_btn.click(
        fetch_interface, 
        inputs=[mode, pdb_input, pdb_file], 
        outputs=molecule_output2
    )

    gr.Markdown("## Examples")
    gr.Examples(
        examples=[
            ["7RPZ", "A"],
            ["2IWI", "B"],
            ["7LCJ", "R"]
        ],
        inputs=[pdb_input, segment_input],
        outputs=[predictions_output, molecule_output, download_output]
    )

demo.launch(share=True)

* Running on local URL:  http://127.0.0.1:7873
* Running on public URL: https://120000a6aa9d78e04c.gradio.live

This share link expires in 72 hours. For free permanent hosting and GPU upgrades, run `gradio deploy` from the terminal in the working directory to deploy to Hugging Face Spaces (https://huggingface.co/spaces)


In [21]:
from datetime import datetime
import gradio as gr
import requests
from Bio.PDB import PDBParser, MMCIFParser, PDBIO, Select, Structure
from Bio.PDB.Polypeptide import is_aa
from Bio.SeqUtils import seq1
from typing import Optional, Tuple, Dict, List
import numpy as np
import os
from gradio_molecule3d import Molecule3D
import torch
import torch.nn as nn
import torch.nn.functional as F
from torch.utils.data import DataLoader
import re
import pandas as pd
import copy
from scipy.special import expit
import logging
import tempfile

# Set up logging
logging.basicConfig(level=logging.INFO)
logger = logging.getLogger(__name__)

class StructureError(Exception):
    """Custom exception for structure-related errors"""
    pass

def normalize_scores(scores: np.ndarray) -> np.ndarray:
    """Normalize scores to range [0,1]"""
    min_score = np.min(scores)
    max_score = np.max(scores)
    return (scores - min_score) / (max_score - min_score) if max_score > min_score else scores

def read_mol(pdb_path: str) -> str:
    """Read molecular structure file and return its content"""
    try:
        with open(pdb_path, 'r') as f:
            return f.read()
    except Exception as e:
        raise IOError(f"Failed to read structure file: {e}")

def fetch_structure(pdb_id: str, output_dir: str = ".") -> Optional[str]:
    """Fetch structure file, trying multiple formats and sources"""
    try:
        # First try local cache
        for ext in ['.cif', '.pdb']:
            local_path = os.path.join(output_dir, f"{pdb_id.lower()}{ext}")
            if os.path.exists(local_path):
                logger.info(f"Using cached structure: {local_path}")
                return local_path

        # Try different download sources
        sources = [
            f"https://files.rcsb.org/download/{pdb_id.upper()}.cif",
            f"https://files.rcsb.org/download/{pdb_id.upper()}.pdb",
            f"https://files.rcsb.org/download/{pdb_id.lower()}.cif",
            f"https://files.rcsb.org/download/{pdb_id.lower()}.pdb"
        ]

        for url in sources:
            try:
                response = requests.get(url, timeout=10)
                if response.status_code == 200:
                    ext = '.cif' if 'cif' in url else '.pdb'
                    file_path = os.path.join(output_dir, f"{pdb_id.lower()}{ext}")
                    with open(file_path, 'wb') as f:
                        f.write(response.content)
                    logger.info(f"Successfully downloaded: {url}")
                    return file_path
            except Exception as e:
                logger.warning(f"Failed to download from {url}: {e}")
                continue

        raise StructureError(f"Failed to fetch structure for PDB ID: {pdb_id}")
    except Exception as e:
        raise StructureError(f"Error fetching structure: {e}")

def convert_cif_to_pdb(cif_path: str, output_dir: str = ".") -> str:
    """Convert CIF to PDB format with error handling"""
    try:
        pdb_path = os.path.join(output_dir, os.path.basename(cif_path).replace('.cif', '.pdb'))
        parser = MMCIFParser(QUIET=True)
        structure = parser.get_structure('protein', cif_path)
        io = PDBIO()
        io.set_structure(structure)
        io.save(pdb_path)
        return pdb_path
    except Exception as e:
        raise StructureError(f"Failed to convert CIF to PDB: {e}")

def find_valid_chain(structure: Structure.Structure) -> Optional[str]:
    """Find the first valid protein chain in the structure"""
    for model in structure:
        for chain in model:
            protein_residues = [res for res in chain if is_aa(res)]
            if len(protein_residues) > 0:
                return chain.id
    return None

def create_chain_specific_pdb(input_pdb: str, chain_id: str, residue_scores: list, protein_residues: list) -> str:
    """Create PDB file with selected chain and prediction scores in B-factor column"""
    class ResidueSelector(Select):
        def __init__(self, chain_id, selected_residues, scores_dict):
            self.chain_id = chain_id
            self.selected_residues = selected_residues
            self.scores_dict = scores_dict
        
        def accept_chain(self, chain):
            return chain.id == self.chain_id
        
        def accept_residue(self, residue):
            return residue.id[1] in self.selected_residues

        def accept_atom(self, atom):
            if atom.parent.id[1] in self.scores_dict:
                atom.bfactor = np.absolute(1-self.scores_dict[atom.parent.id[1]]) * 100
            return True

    try:
        parser = PDBParser(QUIET=True)
        structure = parser.get_structure('protein', input_pdb)
        output_pdb = f"{os.path.splitext(input_pdb)[0]}_{chain_id}_predictions_scores.pdb"
        scores_dict = {resi: score for resi, score in residue_scores}
        
        io = PDBIO()
        selector = ResidueSelector(chain_id, [res.id[1] for res in protein_residues], scores_dict)
        io.set_structure(structure[0])
        io.save(output_pdb, selector)
        
        return output_pdb
    except Exception as e:
        raise StructureError(f"Failed to create chain-specific PDB: {e}")

def process_pdb(pdb_id_or_file: str, segment: str) -> Tuple[str, str, List[str]]:
    """Process PDB/CIF file and generate visualizations and predictions"""
    try:
        # Handle input
        if pdb_id_or_file.endswith(('.pdb', '.cif')):
            pdb_path = pdb_id_or_file
            pdb_id = os.path.splitext(os.path.basename(pdb_path))[0]
        else:
            pdb_id = pdb_id_or_file
            pdb_path = fetch_structure(pdb_id)

        if not pdb_path:
            raise StructureError("Failed to obtain structure file")

        # Parse structure
        parser = MMCIFParser(QUIET=True) if pdb_path.endswith('.cif') else PDBParser(QUIET=True)
        structure = parser.get_structure('protein', pdb_path)

        # Handle chain selection
        if segment == 'auto' or not segment:
            segment = find_valid_chain(structure)
            if not segment:
                raise StructureError("No valid protein chains found in structure")
        
        try:
            chain = structure[0][segment]
        except KeyError:
            valid_chain = find_valid_chain(structure)
            if valid_chain:
                chain = structure[0][valid_chain]
                segment = valid_chain
                logger.info(f"Using alternative chain {segment}")
            else:
                raise StructureError(f"Invalid chain ID '{segment}'. Structure has no valid protein chains.")

        # Process chain
        protein_residues = [res for res in chain if is_aa(res)]
        if not protein_residues:
            raise StructureError(f"No amino acid residues found in chain {segment}")

        sequence = "".join(seq1(res.resname) for res in protein_residues)
        sequence_id = [res.id[1] for res in protein_residues]
        
        # Generate predictions (currently random)
        scores = np.random.rand(len(sequence))
        normalized_scores = normalize_scores(scores)
        residue_scores = [(resi, score) for resi, score in zip(sequence_id, normalized_scores)]

        # Generate outputs
        result_str = generate_results_string(pdb_id, segment, protein_residues, normalized_scores, sequence)
        scored_pdb = create_chain_specific_pdb(pdb_path, segment, residue_scores, protein_residues)
        mol_vis = molecule(pdb_path, residue_scores, segment)
        pymol_commands = generate_pymol_commands(pdb_id, segment, residue_scores, pdb_path)

        # Save results
        prediction_file = f"{pdb_id}_binding_site_residues.txt"
        with open(prediction_file, "w") as f:
            f.write(result_str)

        return pymol_commands, mol_vis, [prediction_file, scored_pdb]

    except StructureError as e:
        return str(e), None, None
    except Exception as e:
        return f"An unexpected error occurred: {str(e)}", None, None

def generate_results_string(pdb_id: str, segment: str, protein_residues: list, 
                          normalized_scores: np.ndarray, sequence: str) -> str:
    """Generate formatted results string with predictions"""
    score_brackets = {
        "0.0-0.2": (0.0, 0.2),
        "0.2-0.4": (0.2, 0.4),
        "0.4-0.6": (0.4, 0.6),
        "0.6-0.8": (0.6, 0.8),
        "0.8-1.0": (0.8, 1.0)
    }
    
    residues_by_bracket = {bracket: [] for bracket in score_brackets}
    
    # Categorize residues
    for i, score in enumerate(normalized_scores):
        for bracket, (lower, upper) in score_brackets.items():
            if lower <= score < upper:
                residues_by_bracket[bracket].append(protein_residues[i])
                break
    
    # Format results
    current_time = datetime.now().strftime("%Y-%m-%d %H:%M:%S")
    result_str = f"""Prediction Results
========================
PDB: {pdb_id}
Chain: {segment}
Date: {current_time}

Analysis by Score Brackets
========================
"""
    
    for bracket, residues in residues_by_bracket.items():
        if residues:  # Only show brackets with residues
            result_str += f"\nBracket {bracket}:\n"
            result_str += "ResName ResNum Code Score\n"
            result_str += "-" * 30 + "\n"
            result_str += "\n".join([
                f"{res.resname:6} {res.id[1]:6} {sequence[i]:4} {normalized_scores[i]:6.2f}" 
                for i, res in enumerate(protein_residues) if res in residues
            ])
            result_str += "\n"
    
    return result_str

def generate_pymol_commands(pdb_id: str, segment: str, residue_scores: list, pdb_path: str) -> str:
    """Generate PyMOL visualization commands"""
    # Group residues by score ranges
    score_groups = {
        "very_low": [], "low": [], "medium": [], "high": [], "very_high": []
    }
    
    for resi, score in residue_scores:
        if score <= 0.2:
            score_groups["very_low"].append(str(resi))
        elif score <= 0.4:
            score_groups["low"].append(str(resi))
        elif score <= 0.6:
            score_groups["medium"].append(str(resi))
        elif score <= 0.8:
            score_groups["high"].append(str(resi))
        else:
            score_groups["very_high"].append(str(resi))

    current_time = datetime.now().strftime("%Y-%m-%d %H:%M:%S")
    commands = f"""# PyMOL Script for {pdb_id} Chain {segment}
# Generated: {current_time}

# Load structure and set initial display
load {os.path.abspath(pdb_path)}, protein
bg_color white
hide everything
show cartoon, chain {segment}
color white, chain {segment}

# Create selection groups by score
"""
    
    color_scheme = {
        "very_low": "white",
        "low": "lightorange",
        "medium": "orange",
        "high": "orangered",
        "very_high": "red"
    }
    
    for group, residues in score_groups.items():
        if residues:
            resi_str = "+".join(residues)
            commands += f"""
# {group.replace('_', ' ').title()} scoring residues
select {group}, chain {segment} and resi {resi_str}
show sticks, {group}
color {color_scheme[group]}, {group}"""
    
    commands += """

# Center and zoom
center chain {}
zoom chain {}
"""

    return commands

def molecule(input_pdb: str, residue_scores: list = None, segment: str = 'A') -> str:
    """Generate interactive 3D molecule visualization"""
    try:
        mol = read_mol(input_pdb)
    except Exception as e:
        return f'<div class="error">Error loading structure: {str(e)}</div>'

    # Prepare residue groups for visualization
    vis_groups = {
        "class1": [],  # 0.0-0.2
        "class2": [],  # 0.2-0.4
        "class3": [],  # 0.4-0.6
        "class4": [],  # 0.6-0.8
        "class5": []   # 0.8-1.0
    }

    if residue_scores:
        for resi, score in residue_scores:
            if score <= 0.2:
                vis_groups["class1"].append(resi)
            elif score <= 0.4:
                vis_groups["class2"].append(resi)
            elif score <= 0.6:
                vis_groups["class3"].append(resi)
            elif score <= 0.8:
                vis_groups["class4"].append(resi)
            else:
                vis_groups["class5"].append(resi)

    # Generate visualization script
    vis_script = f"""
        // Base model setup
        let chainModel = viewer.addModel(pdb, "pdb");
        chainModel.setStyle({{}}, {{}});
        chainModel.setStyle(
            {{"chain": "{segment}"}}, 
            {{"cartoon": {{"color": "white"}}}}
        );
    """

    # Color schemes for different score ranges
    color_schemes = {
        "class1": {"color": "0xFFFFFF", "opacity": 0.5},  # White
        "class2": {"color": "0xFFD580", "opacity": 0.7},  # Light orange
        "class3": {"color": "0xFFA500", "opacity": 1.0},  # Orange
        "class4": {"color": "0xFF4500", "opacity": 1.0},  # Orange red
        "class5": {"color": "0xFF0000", "opacity": 1.0}   # Red
    }

    # Add visualization for each group
    for group, residues in vis_groups.items():
        if residues:
            color_scheme = color_schemes[group]
            vis_script += f"""
        let {group}Model = viewer.addModel(pdb, "pdb");
        {group}Model.setStyle({{}}, {{}});
        {group}Model.setStyle(
            {{"chain": "{segment}", "resi": [{", ".join(map(str, residues))}]}},
            {{"stick": {{"color": "{color_scheme["color"]}", "opacity": {color_scheme["opacity"]}}}}}
        );
        """

    # Generate full HTML with enhanced controls and information
    html_content = f"""
    <!DOCTYPE html>
    <html>
    <head>    
        <meta http-equiv="content-type" content="text/html; charset=UTF-8" />
        <style>
        .mol-container {{
            width: 100%;
            height: 700px;
            position: relative;
        }}
        .controls {{
            position: absolute;
            top: 10px;
            left: 10px;
            background: rgba(255, 255, 255, 0.8);
            padding: 10px;
            border-radius: 5px;
            z-index: 1000;
        }}
        .legend {{
            position: absolute;
            bottom: 10px;
            right: 10px;
            background: rgba(255, 255, 255, 0.8);
            padding: 10px;
            border-radius: 5px;
            z-index: 1000;
        }}
        .error {{
            color: red;
            padding: 20px;
            text-align: center;
            font-weight: bold;
        }}
        </style>
        <script src="https://cdnjs.cloudflare.com/ajax/libs/jquery/3.6.3/jquery.min.js"></script>
        <script src="https://3Dmol.csb.pitt.edu/build/3Dmol-min.js"></script>
    </head>
    <body>
        <div id="container" class="mol-container">
            <div class="controls">
                <button onclick="toggleStyle('cartoon')">Toggle Cartoon</button>
                <button onclick="toggleStyle('stick')">Toggle Sticks</button>
                <button onclick="resetView()">Reset View</button>
                <button onclick="toggleSpin()">Toggle Spin</button>
            </div>
            <div class="legend">
                <div><span style="color: #FF0000">■</span> Very High (0.8-1.0)</div>
                <div><span style="color: #FF4500">■</span> High (0.6-0.8)</div>
                <div><span style="color: #FFA500">■</span> Medium (0.4-0.6)</div>
                <div><span style="color: #FFD580">■</span> Low (0.2-0.4)</div>
                <div><span style="color: #FFFFFF">■</span> Very Low (0.0-0.2)</div>
            </div>
        </div>
        <script>
            let pdb = `{mol}`;
            let viewer;
            let isSpinning = false;

            $(document).ready(function () {{
                let element = $("#container");
                let config = {{ backgroundColor: "white" }};
                viewer = $3Dmol.createViewer(element, config);
                
                {vis_script}
                
                // Enhanced hover functionality
                viewer.setHoverable(
                    {{}}, 
                    true, 
                    function(atom, viewer, event, container) {{
                        if (!atom.label) {{
                            atom.label = viewer.addLabel(
                                `${{atom.resn}}:${{atom.resi}}:${{atom.atom}}`, 
                                {{
                                    position: atom, 
                                    backgroundColor: 'mintcream', 
                                    fontColor: 'black',
                                    fontSize: 18,
                                    padding: 4
                                }}
                            );
                        }}
                    }},
                    function(atom, viewer) {{
                        if (atom.label) {{
                            viewer.removeLabel(atom.label);
                            delete atom.label;
                        }}
                    }}
                );
                
                viewer.zoomTo();
                viewer.render();
                viewer.zoom(0.8, 2000);
            }});

            function toggleStyle(style) {{
                let elements = viewer.selectedAtoms({{}});
                let currentStyle = elements.style[style];
                elements.style[style] = !currentStyle;
                viewer.render();
            }}

            function resetView() {{
                viewer.zoomTo();
                viewer.render();
            }}

            function toggleSpin() {{
                isSpinning = !isSpinning;
                viewer.spin(isSpinning);
            }}
        </script>
    </body>
    </html>
    """
    
    return f'<iframe width="100%" height="700" srcdoc="{html_content.replace(chr(34), "&quot;").replace(chr(39), "&#39;")}"></iframe>'

# Gradio UI
def create_ui():
    with gr.Blocks(title="Protein Binding Site Prediction", theme=gr.themes.Base()) as demo:
        gr.Markdown("""
        # Protein Binding Site Prediction
        
        This tool helps you visualize and analyze potential binding sites in protein structures.
        You can either:
        1. Enter a PDB ID (e.g., "4BDU")
        2. Upload your own PDB/CIF file
        
        The tool will analyze the structure and show predictions using a color gradient from white (low probability) to red (high probability).
        """)
        
        with gr.Row():
            with gr.Column(scale=2):
                # Input components
                mode = gr.Radio(
                    choices=["PDB ID", "Upload File"],
                    value="PDB ID",
                    label="Input Mode",
                    info="Choose whether to input a PDB ID or upload a PDB/CIF file"
                )
                
                with gr.Group():
                    pdb_input = gr.Textbox(
                        value="4BDU",
                        label="PDB ID",
                        placeholder="Enter PDB ID (e.g., 4BDU)",
                        info="Enter a valid PDB ID from the Protein Data Bank"
                    )
                    pdb_file = gr.File(
                        label="Upload PDB/CIF File",
                        file_types=[".pdb", ".cif"],
                        visible=False
                    )
                
                segment_input = gr.Textbox(
                    value="A",
                    label="Chain ID",
                    placeholder="Enter Chain ID or leave empty for automatic selection",
                    info="Specify which protein chain to analyze, or leave empty for automatic selection"
                )

            with gr.Column(scale=1):
                visualize_btn = gr.Button("Visualize Structure", variant="primary")
                prediction_btn = gr.Button("Predict Binding Site", variant="secondary")
                
                gr.Markdown("""
                ### Color Legend
                - White: Very Low (0.0-0.2)
                - Light Orange: Low (0.2-0.4)
                - Orange: Medium (0.4-0.6)
                - Orange Red: High (0.6-0.8)
                - Red: Very High (0.8-1.0)
                """)

        with gr.Tab("3D Visualization"):
            molecule_output = gr.HTML(label="Interactive 3D Structure")
            
        with gr.Tab("Analysis Results"):
            predictions_output = gr.Textbox(
                label="PyMOL Visualization Commands",
                info="Copy these commands into PyMOL to recreate the visualization"
            )
            download_output = gr.File(
                label="Download Results",
                file_count="multiple"
            )

        # Error message container
        error_output = gr.Markdown(visible=False)

        # Mode change handler
        def toggle_mode(selected_mode):
            return {
                pdb_input: gr.update(visible=selected_mode == "PDB ID"),
                pdb_file: gr.update(visible=selected_mode == "Upload File")
            }

        mode.change(
            toggle_mode,
            inputs=[mode],
            outputs=[pdb_input, pdb_file]
        )

        # Process handlers
        def handle_visualization(mode, pdb_id, pdb_file):
            try:
                result = fetch_interface(mode, pdb_id, pdb_file)
                if isinstance(result, str) and result.startswith("Error"):
                    return None, gr.update(visible=True, value=f"```\n{result}\n```")
                return result, gr.update(visible=False)
            except Exception as e:
                return None, gr.update(visible=True, value=f"```\nError: {str(e)}\n```")

        def handle_prediction(mode, pdb_id, pdb_file, chain_id):
            try:
                predictions, vis, downloads = process_interface(mode, pdb_id, pdb_file, chain_id)
                if isinstance(predictions, str) and "Error" in predictions:
                    return (
                        None,
                        None,
                        None,
                        gr.update(visible=True, value=f"```\n{predictions}\n```")
                    )
                return (
                    predictions,
                    vis,
                    downloads,
                    gr.update(visible=False)
                )
            except Exception as e:
                error_msg = f"""Error processing structure:
```
{str(e)}

Troubleshooting tips:
1. Check if the PDB ID is valid
2. Ensure the Chain ID exists in the structure
3. Try leaving Chain ID empty for automatic selection
4. If uploading a file, ensure it's a valid PDB/CIF format
```"""
                return None, None, None, gr.update(visible=True, value=error_msg)

        def fetch_interface(mode, pdb_id, pdb_file):
            try:
                if mode == "PDB ID":
                    if not pdb_id or len(pdb_id.strip()) != 4:
                        raise ValueError("Please enter a valid 4-character PDB ID")
                    return fetch_pdb(pdb_id.strip())
                elif mode == "Upload File":
                    if not pdb_file:
                        raise ValueError("Please upload a PDB or CIF file")
                    _, ext = os.path.splitext(pdb_file.name)
                    if ext.lower() not in ['.pdb', '.cif']:
                        raise ValueError("Only .pdb and .cif files are supported")
                    
                    # Create temp directory for file handling
                    with tempfile.TemporaryDirectory() as temp_dir:
                        temp_path = os.path.join(temp_dir, os.path.basename(pdb_file.name))
                        with open(temp_path, 'wb') as f:
                            f.write(pdb_file.read())
                        
                        if ext.lower() == '.cif':
                            return convert_cif_to_pdb(temp_path)
                        return temp_path
                else:
                    raise ValueError("Invalid mode selected")
            except Exception as e:
                return f"Error: {str(e)}"

        # Connect event handlers
        visualize_btn.click(
            handle_visualization,
            inputs=[mode, pdb_input, pdb_file],
            outputs=[molecule_output, error_output]
        )

        prediction_btn.click(
            handle_prediction,
            inputs=[mode, pdb_input, pdb_file, segment_input],
            outputs=[predictions_output, molecule_output, download_output, error_output]
        )

        # Add examples
        gr.Examples(
            examples=[
                ["PDB ID", "7RPZ", None, "A"],
                ["PDB ID", "2IWI", None, "B"],
                ["PDB ID", "2F6V", None, "A"]
            ],
            inputs=[mode, pdb_input, pdb_file, segment_input],
            outputs=[predictions_output, molecule_output, download_output, error_output],
            fn=handle_prediction,
            cache_examples=True
        )

        # Add documentation
        gr.Markdown("""
        ## Usage Instructions
        
        1. **Input Structure:**
           - Enter a PDB ID (e.g., "4BDU") or upload your own structure file
           - The tool supports both PDB (.pdb) and mmCIF (.cif) formats
        
        2. **Select Chain:**
           - Enter a specific chain ID (e.g., "A")
           - Leave empty for automatic selection of the first valid protein chain
        
        3. **Analyze:**
           - Click "Visualize Structure" to view the 3D structure
           - Click "Predict Binding Site" to perform binding site analysis
        
        4. **Results:**
           - Interactive 3D visualization with color-coded predictions
           - PyMOL commands for external visualization
           - Downloadable results files
        
        ## Troubleshooting
        
        If you encounter issues:
        1. Ensure your PDB ID is valid and exists in the PDB database
        2. Check that your uploaded file is a valid PDB/CIF format
        3. Try automatic chain selection if your specified chain isn't found
        4. Clear your browser cache if visualizations don't load
        """)

    return demo

if __name__ == "__main__":
    demo = create_ui()
    demo.launch(share=True)

/home/frohlkin/anaconda3/envs/LLM/lib/python3.12/site-packages/gradio/helpers.py:441: UserWarning: Examples will be cached but not all input components have example values. This may result in an exception being thrown by your function. If you do get an error while caching examples, make sure all of your inputs have example values for all of your examples or you provide default values for those particular parameters in your function.
  warnings.warn(
INFO:__main__:Using cached structure: ./7rpz.cif
INFO:__main__:Using cached structure: ./2iwi.cif
INFO:__main__:Using cached structure: ./2f6v.cif
INFO:httpx:HTTP Request: GET http://127.0.0.1:7862/gradio_api/startup-events "HTTP/1.1 200 OK"


* Running on local URL:  http://127.0.0.1:7862
Caching examples at: '/home/frohlkin/Projects/LargeLanguageModels/Publication/test_webpage/.gradio/cached_examples/148'


INFO:httpx:HTTP Request: HEAD http://127.0.0.1:7862/ "HTTP/1.1 200 OK"
INFO:httpx:HTTP Request: GET https://api.gradio.app/pkg-version "HTTP/1.1 200 OK"
INFO:httpx:HTTP Request: GET https://api.gradio.app/v3/tunnel-request "HTTP/1.1 200 OK"


* Running on public URL: https://de785d7cce806497e9.gradio.live

This share link expires in 72 hours. For free permanent hosting and GPU upgrades, run `gradio deploy` from the terminal in the working directory to deploy to Hugging Face Spaces (https://huggingface.co/spaces)


INFO:httpx:HTTP Request: HEAD https://de785d7cce806497e9.gradio.live "HTTP/1.1 200 OK"


Traceback (most recent call last):
  File "/home/frohlkin/anaconda3/envs/LLM/lib/python3.12/site-packages/gradio/routes.py", line 990, in predict
    output = await route_utils.call_process_api(
             ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
  File "/home/frohlkin/anaconda3/envs/LLM/lib/python3.12/site-packages/gradio/route_utils.py", line 322, in call_process_api
    output = await app.get_blocks().process_api(
             ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
  File "/home/frohlkin/anaconda3/envs/LLM/lib/python3.12/site-packages/gradio/blocks.py", line 2047, in process_api
    result = await self.call_function(
             ^^^^^^^^^^^^^^^^^^^^^^^^^
  File "/home/frohlkin/anaconda3/envs/LLM/lib/python3.12/site-packages/gradio/blocks.py", line 1594, in call_function
    prediction = await anyio.to_thread.run_sync(  # type: ignore
                 ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
  File "/home/frohlkin/anaconda3/envs/LLM/lib/python3.12/site-packages/anyio/to_thread.py",